# Author: Intan K. Wardhani

This Jupyter Notebook has been copied from BeCode Arai 8 2025 bootcamp and edited by the aforementioned author.

## Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## 0. Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it and add it to you `.gitignore` file. 

You will find more info about virtual environments in the course content and on the web.

## 1. API Scraping

### 1a. A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword. NOTE: external libraries need to be installed first. Check the [request Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the documentation to:

1. Use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. Check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is an explanation of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [3]:
# import the requests library (1 line)
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.onrender.com"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = "https://country-leaders.onrender.com/status/"

# query the /status endpoint using the get() method and store it in the req variable (1 line)
req_status = requests.get(status_url, timeout=5)

# check the status_code using a condition and print appropriate messages (4 lines)
if req_status == 200:
    print(req_status.text)
else:
    print(req_status.status_code)


200


### 1b. Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. 


In [4]:
# Set the countries_url variable (1 line)
countries_url = "https://country-leaders.onrender.com/countries/"

# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req_countries = requests.get(countries_url, timeout=5)

# Get the JSON content and store it in the countries variable (1 line)
countries = req_countries.json()

# display the request's status code and the countries variable (1 line)
print(req_countries.status_code, countries)


403 {'message': 'The cookie is missing'}


### 1c. Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [5]:
# Set the cookie_url variable (1 line)
cookie_url = "https://country-leaders.onrender.com/cookie/"

# Query the endpoint, set the cookies variable and display it (2 lines)
cookies = requests.get(cookie_url, timeout=5)
print(cookies.status_code, cookies.cookies)


200 <RequestsCookieJar[<Cookie user_cookie=0ef16547-6625-467a-a8b0-2ea60a5f3890 for country-leaders.onrender.com/>]>


Try to query the countries endpoint using the cookie, save the output and print it.

In [6]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(countries_url, cookies=cookies.cookies, timeout=5)

# display the countries variable (1 line)
print(countries.json())


['be', 'us', 'ru', 'fr', 'ma']


Chances are the cookie has expired... Thankfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Added by author
Alternatively, use a session to persist cookies.

In [19]:
# Create a session object to persist cookies
session = requests.Session()

cookie_url = "https://country-leaders.onrender.com/cookie/"
cookies = session.get(cookie_url, timeout=5)

countries_url = "https://country-leaders.onrender.com/countries/"
countries = session.get(countries_url, timeout=5)
countries_data = countries.json()

print(countries.status_code)
print(countries_data)

200
['be', 'us', 'ru', 'fr', 'ma']


### 1d. Getting the actual data from the API

Query the `/leaders` endpoint.

In [14]:
# Set the leaders_url variable (1 line)
leaders_url = "https://country-leaders.onrender.com/leaders"

# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = session.get(leaders_url, cookies=cookies.cookies, timeout=5)

# display the leaders variable (1 line)
print(leaders.json())


{'message': 'Please specify a country'}


It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [ ]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
# assign the output to the leaders variable (1 line)
leaders = session.get(leaders_url, cookies=cookies.cookies, timeout=5, params={'country': countries.json()[0]})

# display the leaders variable (1 line)
print(leaders.json())

[{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'https://nl

### 1e. A sneak peek at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [ ]:
# 4 lines
leaders_per_country = dict()
for country in countries.json():
    leaders = session.get(leaders_url, cookies=cookies.cookies, timeout=5, params={'country': country}).json()
    leaders_per_country[country] = leaders


In [20]:
# or 1 line
leaders_per_country = {
    country: session.get(
        leaders_url, 
        cookies=cookies.cookies, 
        timeout=5, 
        params={'country': country}
        ).json()
    for country in countries.json()
}


In [71]:
print(leaders_per_country['ru'])

[{'id': 'Q7747', 'first_name': 'Vladimir', 'last_name': 'Putin', 'birth_date': '1952-10-07', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9F%D1%83%D1%82%D0%B8%D0%BD,_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80_%D0%92%D0%BB%D0%B0%D0%B4%D0%B8%D0%BC%D0%B8%D1%80%D0%BE%D0%B2%D0%B8%D1%87', 'start_mandate': '2000-05-07', 'end_mandate': '2008-05-07'}, {'id': 'Q23530', 'first_name': 'Dmitry', 'last_name': 'Medvedev', 'birth_date': '1965-09-14', 'death_date': None, 'place_of_birth': 'Saint Petersburg', 'wikipedia_url': 'https://ru.wikipedia.org/wiki/%D0%9C%D0%B5%D0%B4%D0%B2%D0%B5%D0%B4%D0%B5%D0%B2,_%D0%94%D0%BC%D0%B8%D1%82%D1%80%D0%B8%D0%B9_%D0%90%D0%BD%D0%B0%D1%82%D0%BE%D0%BB%D1%8C%D0%B5%D0%B2%D0%B8%D1%87', 'start_mandate': '2008-05-07', 'end_mandate': '2012-05-07'}, {'id': 'Q34453', 'first_name': 'Boris', 'last_name': 'Yeltsin', 'birth_date': '1931-02-01', 'death_date': '2007-04-23', 'place_of_birth': 'Butka', 'wikipedia_url

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [48]:
# < 15 lines
import requests

# set polite user-agent
headers = {
            "User-Agent": f"wikipedia-scraper/0.1 (+https://country-leaders.onrender.com)"
        }
session = requests.Session()
session.headers.update(headers)

def get_leaders() -> dict:
    
    timeout = 5
    
    # define urls
    countries_url = "https://country-leaders.onrender.com/countries/"
    cookie_url = "https://country-leaders.onrender.com/cookie/"
    leaders_url = "https://country-leaders.onrender.com/leaders"
    
    # get the cookies
    cookies = session.get(cookie_url, timeout=timeout)
    
    # get the countries
    countries = session.get(countries_url, timeout=timeout).json()
    
    # loop over countries and save the leaders in a dict
    leaders_per_country = {
                            country: session.get(
                                leaders_url, 
                                cookies=cookies.cookies, 
                                timeout=timeout, 
                                params={'country': country}
                                ).json()
                            for country in countries
                        }
    
    # return the dict
    return leaders_per_country

Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [49]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)

{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'None', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url': 'htt

## 2. Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [118]:
# 3 lines
sample_lead = leaders_per_country['ru'][0]
req_sample_lead = session.get(sample_lead['wikipedia_url'], timeout=5)
print(req_sample_lead.text)

<!DOCTYPE html>
<html class="client-nojs" lang="ru" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Путин, Владимир Владимирович — Википедия</title>
<script>(function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\w+$|[^\w-]+/g,'')+'-clientpref-\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"f01f81d1-fb96-4e67-8061-b3c0f498667a","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Путин,_Владимир_Владимирович","wgTitle":"Путин, Владимир Владимирович","wgC

### Added by author
Turn the code above into a function to get each leader's url.

In [124]:
def get_url(country_code: str, leader_index: int) -> requests.models.Response:
    
    sample_lead = leaders_per_country[country_code][leader_index]
    req_sample_lead = session.get(sample_lead['wikipedia_url'], timeout=5)
    
    return req_sample_lead
    

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [119]:
# 3 lines
from bs4 import BeautifulSoup
soup = BeautifulSoup(req_sample_lead.text, 'html.parser')
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="ru">
 <head>
  <meta charset="utf-8"/>
  <title>
   Путин, Владимир Владимирович — Википедия
  </title>
  <script>
   (function(){var className="client-js";var cookie=document.cookie.match(/(?:^|; )ruwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\w+$|[^\w-]+/g,'')+'-clientpref-\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","январь","февраль","март","апрель","май","июнь","июль","август","сентябрь","октябрь","ноябрь","декабрь"],"wgRequestId":"f01f81d1-fb96-4e67-8061-b3c0f498667a","wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Путин,_Владимир_Владимирович","wgTitle":"Путин, Владимир

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [120]:
# 2 lines
paragraphs = soup.find_all('p')
print(len(paragraphs), type(paragraphs), paragraphs)

308 <class 'bs4.element.ResultSet'> [<p><b>Влади́мир Влади́мирович Пу́тин</b> (род. <a href="/wiki/7_%D0%BE%D0%BA%D1%82%D1%8F%D0%B1%D1%80%D1%8F" title="7 октября">7 октября</a> <a href="/wiki/1952_%D0%B3%D0%BE%D0%B4" title="1952 год">1952</a>, <a href="/wiki/%D0%A1%D0%B0%D0%BD%D0%BA%D1%82-%D0%9F%D0%B5%D1%82%D0%B5%D1%80%D0%B1%D1%83%D1%80%D0%B3" title="Санкт-Петербург">Ленинград</a>, <a href="/wiki/%D0%A1%D0%BE%D1%8E%D0%B7_%D0%A1%D0%BE%D0%B2%D0%B5%D1%82%D1%81%D0%BA%D0%B8%D1%85_%D0%A1%D0%BE%D1%86%D0%B8%D0%B0%D0%BB%D0%B8%D1%81%D1%82%D0%B8%D1%87%D0%B5%D1%81%D0%BA%D0%B8%D1%85_%D0%A0%D0%B5%D1%81%D0%BF%D1%83%D0%B1%D0%BB%D0%B8%D0%BA" title="Союз Советских Социалистических Республик">СССР</a>) — <a href="/wiki/%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D1%8F" title="Россия">российский</a> <a href="/wiki/%D0%93%D0%BE%D1%81%D1%83%D0%B4%D0%B0%D1%80%D1%81%D1%82%D0%B2%D0%BE" title="Государство">государственный</a> и <a href="/wiki/%D0%9F%D0%BE%D0%BB%D0%B8%D1%82%D0%B8%D0%BA%D0%B0" title="Политика">политический</a

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one:
   * Store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
   * Exit the loop

### Added by author
First, try my solution in this sandbox.
It seems that on almost all wiki pages, the main content lives inside `<div id="mw-content-text">` and `<div class="mw-parser-output">`. So, I will try to extract paragraphs that sit only in these divisions.  
I want to make sure that the first `<p>`tag:  
* contains text
* is not empty
* is not part of an infobox, notice box, redirect message, etc.

In [ ]:
# Find the main content div
# content_div = soup.find('div', class_='mw-parser-output')
# for p in content_div.find_all('p'):

for p in soup.select("div.mw-parser-output p"):
    text = p.get_text(strip=True)
    if not text:
        continue # skip empty text
    if 'redirected from' in text.lower():
        continue # skip redirect messages
    if p.find_parent('table') or p.find_parent('div', class_='hatnote'):
        continue # skip infoboxes, notices, etc.
    print(text)
    break # stop after first paragraph

        



Влади́мир Влади́мирович Пу́тин(род.7 октября1952,Ленинград,СССР) —российскийгосударственныйиполитическийдеятель. Действующийпрезидент Российской Федерации, председательГосударственного Совета Российской ФедерациииСовета Безопасности Российской Федерации;Верховный главнокомандующий Вооружёнными силами Российской Федерациис 7 мая 2012 года. Ранее занимал должность президента с 7 мая 2000 по 7 мая 2008 года, также в 1999—2000 и 2008—2012 годах занимал должностьпредседателя правительства Российской Федерации.Де-факторуководит Россией, согласно разным оценкам, с1999[5]или с2000года[6].


The problem with finding content division is that it doesn't work for the wiki pages in Arabic. After a good while, I have found that looping through the paragraphs using a CSS selector `soup_select()` works better. It works at least for the pages in this project.

Below is the actual solution.

In [ ]:
# <=10 lines
for p in soup.select("div.mw-parser-output p"):
    text = p.get_text(strip=True)
    if not text:
        continue # skip empty text
    if 'redirected from' in text.lower():
        continue # skip redirect messages
    if p.find_parent('table') or p.find_parent('div', class_='hatnote'):
        continue # skip infoboxes, notices, etc.
    print(text)
    break # stop after first paragraph


At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [136]:
# 10 lines
# def get_first_paragraph(wikipedia_url):
#   print(wikipedia_url) # keep this for the rest of the notebook
#   [insert your code]
#   return first_paragraph

def get_first_paragraph(wiki_url: requests.models.Response) -> tuple:
    
    """A function to get only the first paragraph from a wiki page."""
    
    soup = BeautifulSoup(wiki_url.text, 'html.parser')
    lang = soup.html.get("lang") if soup.html else "unknown" # i wanna know the language
    first_paragraph = ""
    for p in soup.select("div.mw-parser-output p"):
        text = p.get_text(strip=True)
        if not text:
            continue # skip empty text
        if 'redirected from' in text.lower():
            continue # skip redirect messages
        if p.find_parent('table') or p.find_parent('div', class_='hatnote'):
            continue # skip infoboxes, notices, etc.
        first_paragraph = text
        break # stop after first paragraph
    
    return lang, first_paragraph

In [148]:
# Test: 3 lines

wiki_url = get_url('us', 1)
_, first_paragraph = get_first_paragraph(wiki_url)
print(first_paragraph)

Barack Hussein Obama II[a](born August 4, 1961) is an American politician who served as the 44thpresident of the United Statesfrom 2009 to 2017. A member of theDemocratic Party, he was the firstAfrican Americanpresident. Obama previously served as aU.S. senatorrepresenting Illinois from 2005 to 2008 and as anIllinois state senatorfrom 1997 to 2004.


### 2a. Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but others do not.

In [161]:
# 3 lines

import re

# 1️⃣ Remove reference-style notes like [a], [1], [note 2]
text = re.sub(r'\[[^\]]*\]', '', first_paragraph)

# 2️⃣ Ensure a space after closing parentheses or punctuation if missing
text = re.sub(r'([a-z\)])([A-Z])', r'\1 \2', text)  # e.g., ")i" -> ") i"

# 3️⃣ Add missing spaces between words stuck together (lowercase + uppercase)
text = re.sub(r'([a-z])([A-Z])', r'\1 \2', text)

# 4️⃣ Fix glued numbers/words: 44thpresident → 44th president
# text = re.sub(r'(\d)([A-Za-z])', r'\1 \2', text)
text = re.sub(r'(\d[a-z][a-z])([a-z])', r'\1 \2', text)

# 5️⃣ Add missing space after known words when glued
# e.g., "theDemocratic" → "the Democratic"
text = re.sub(r'([a-z])([A-Z])', r'\1 \2', text)

# 6️⃣ Fix cases like "Statesfrom" → "States from"
text = re.sub(r'([a-z])([A-Z])', r'\1 \2', text)

# 7️⃣ Add space after periods if missing (e.g. "2004.He" → "2004. He")
text = re.sub(r'\.([A-Z])', r'. \1', text)

# 8️⃣ Handle “aU.S.” → “a U.S.”
text = re.sub(r'([a-z])([A-Z]\.)', r'\1 \2', text)

# 9️⃣ Normalize whitespace (collapse multiple spaces)
text = re.sub(r'\s+', ' ', text).strip()

print(text)


Barack Hussein Obama II(born August 4, 1961) is an American politician who served as the 44th president of the United Statesfrom 2009 to 2017. A member of the Democratic Party, he was the first African Americanpresident. Obama previously served as a U. S. senatorrepresenting Illinois from 2005 to 2008 and as an Illinois state senatorfrom 1997 to 2004.


Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [ ]:
# 10 lines


Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [ ]:
# < 20 lines


## 3. Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [ ]:
# < 20 lines

In [ ]:
# Check the output of your function (2 lines)


Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [ ]:
# < 25 lines



Check the output of your function again.

In [ ]:
# Check the output of your function (1 line)


Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [ ]:
# < 20 lines


Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [ ]:
# <25 lines


Test your new functions.



## 4. Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [ ]:
# 3 lines


Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [ ]:
# 3 lines


Make a function `save(leaders_per_country)` to call this code easily.

In [ ]:
# 3 lines


In [ ]:
# Call the function (1 line)


## 5. Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## (Optional) To go further

If you want to practice scraping, you can read this section and tackle the exercises.

1. Restructure your code by using OOP (see ReadMe).
2. You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!